In [ ]:
!pip install pystan==2.19.1.1 --quiet
!pip install fbprophet --quiet
!pip install yfinance --quiet

In [ ]:
pip install yfinance

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 6.4 MB 7.1 MB/s 
     |████████████████████████████████| 63 kB 1.4 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0
  Attempting uninstall: lxml
    Found existing installation: lxml 4.2.6
    Uninstalling lxml-4.2.6:
      Successfully uninstalled lxml-4.2.6
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires requests~=2.23.0, but you have requests 2.27.1 which is incompatible.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.8.3 which is incompatible.


In [1]:
import pandas as pd
import yfinance as yf
from datetime import datetime
from datetime import timedelta
import plotly.graph_objects as go
from fbprophet import Prophet
from fbprophet.plot import plot_plotly, plot_components_plotly
import warnings

warnings.filterwarnings('ignore')

pd.options.display.float_format = '${:,.2f}'.format

In [2]:
today = datetime.today().strftime('%Y-%m-%d')
start_date = '2000-09-01'

df = yf.download('GC=F',start_date, today)

df.tail()

[*********************100%***********************]  1 of 1 completed


Open      High       Low     Close  Adj Close  Volume
Date                                                                 
2022-06-02 $1,845.40 $1,868.70 $1,842.10 $1,866.50  $1,866.50     551
2022-06-03 $1,867.60 $1,871.80 $1,845.40 $1,845.40  $1,845.40      53
2022-06-06 $1,849.00 $1,854.10 $1,839.20 $1,839.20  $1,839.20     142
2022-06-07 $1,836.90 $1,851.60 $1,835.00 $1,847.50  $1,847.50    1168
2022-06-08 $1,844.80 $1,855.00 $1,844.40 $1,851.90  $1,851.90    1168

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 5462 entries, 2000-08-31 to 2022-06-08
Data columns (total 6 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   Open       5462 non-null   float64
 1   High       5462 non-null   float64
 2   Low        5462 non-null   float64
 3   Close      5462 non-null   float64
 4   Adj Close  5462 non-null   float64
 5   Volume     5462 non-null   int64  
dtypes: float64(5), int64(1)
memory usage: 298.7 KB


In [4]:
df.isnull().sum()

Open         0
High         0
Low          0
Close        0
Adj Close    0
Volume       0
dtype: int64

In [5]:
df.columns

Index(['Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume'], dtype='object')

In [6]:
df.reset_index(inplace=True)
df.columns

Index(['Date', 'Open', 'High', 'Low', 'Close', 'Adj Close', 'Volume'], dtype='object')

In [7]:
df1 = df[["Date", "Open"]]

new_names = {
    "Date": "ds", 
    "Open": "y",
}

df1.rename(columns=new_names, inplace=True)

In [8]:
df1.tail()

ds         y
5457 2022-06-02 $1,845.40
5458 2022-06-03 $1,867.60
5459 2022-06-06 $1,849.00
5460 2022-06-07 $1,836.90
5461 2022-06-08 $1,844.80

In [9]:
# plot the open price

x = df1["ds"]
y = df1["y"]

fig = go.Figure()

fig.add_trace(go.Scatter(x=x, y=y))

# Set title
fig.update_layout(
    title_text="Time series plot of Gold Open Price",
)

fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list(
                [
                    dict(count=1, label="1m", step="month", stepmode="backward"),
                    dict(count=6, label="6m", step="month", stepmode="backward"),
                    dict(count=1, label="YTD", step="year", stepmode="todate"),
                    dict(count=1, label="1y", step="year", stepmode="backward"),
                    dict(step="all"),
                ]
            )
        ),
        rangeslider=dict(visible=True),
        type="date",
    )
)

In [10]:
m = Prophet(
    seasonality_mode="multiplicative" 
)

m.fit(df1)

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.


In [11]:
future = m.make_future_dataframe(periods = 365)
future.tail()

ds
5822 2023-06-04
5823 2023-06-05
5824 2023-06-06
5825 2023-06-07
5826 2023-06-08

In [12]:
forecast = m.predict(future)
forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds       yhat  yhat_lower  yhat_upper
5822 2023-06-04 $-3,805.51  $-4,053.93  $-3,552.67
5823 2023-06-05  $2,142.74   $1,979.76   $2,303.76
5824 2023-06-06  $2,142.55   $1,973.13   $2,297.28
5825 2023-06-07  $2,144.60   $1,985.06   $2,293.18
5826 2023-06-08  $2,145.67   $1,987.70   $2,292.91

In [13]:
next_day = (datetime.today() + timedelta(days=1)).strftime('%Y-%m-%d')

forecast[forecast['ds'] == next_day]['yhat'].item()

1970.229710766759

In [14]:
check=forecast['ds'][0]

In [15]:
check

Timestamp('2000-08-31 00:00:00')

In [16]:
next_day

'2022-06-10'

In [17]:
next_day1=('2022-07-04')
prediction=forecast[forecast['ds'] == next_day1]['yhat'].item()

In [18]:
type(next_day)

str

In [19]:
prediction

1970.9132813076094

In [20]:
next_day1

'2022-07-04'

In [21]:
plot_plotly(m, forecast)

In [22]:
plot_components_plotly(m, forecast)

In [23]:
import pickle
pickle.dump(m,open('fbgold.pkl','wb'))